In [87]:
import numpy as np
np.random.seed(5)

def compute_poly(x, m, p, poly_power_limit):
    """
    x : m x 1 complex vector
    PolyW : polynomial layer weights
    m : input dimension
    p : polynomial degree
    poly_power_limit : polynomial power limit

    return : a p x m complex vector
    """
    # out put : a nx1 complex vector

    # polynomial 
    u = np.zeros((p, m), dtype=np.complex128)
    for j in range(p): 
        u[j] = np.power(np.abs(x) * poly_power_limit,2*j) * x 
    return u
def compute_poly_sum(u, PolyW):
    """
    u : p x m complex vector
    PolyW : polynomial layer weights
    return : a m x 1 complex vector
    """
    return np.dot(PolyW, u)

def compute_conv(Us, ConvW):
    """
    Us : k x m  complex vector
    ConvW : convolutional layer weights : k x m x m
    return : a 1 x m complex vector
    """
    k, m, m = ConvW.shape ##
    C = np.zeros((m), dtype=np.complex128)

    for i in range(k):
        C += np.dot(Us[i], ConvW[i])
    return C

In [88]:
### generate complex data 

def generate_data(n_samples, true_coefficients, noise_level=0.1, poly_power_limit=0.05):

    # Generate a random input signal
    k,m, n = true_coefficients[0].shape
    p = true_coefficients[1].shape[0]
    ConvW = true_coefficients[0]
    PolyW = true_coefficients[1]

    x = np.random.randn(n_samples, m) + 1j*np.random.randn(n_samples, m)

    # Step 1: Compute the convolution : in n_samples x m and k x m x n , out n_samples x n
    C = np.zeros((n_samples, n), dtype=np.complex128)
    for i in range(k, n_samples):
        C[i] = compute_conv(x[i-k+1 : i+1], ConvW)
    
    # Step 2: Compute the polynomial features: in n_samples x n , out n_samples x p x nn
    U = np.zeros((n_samples, p, n), dtype=np.complex128)
    for i in range(n_samples):
        U[i] = compute_poly(C[i], n, p, poly_power_limit)
    print(U[:10])
    # Step 3: Compute the polynomial sum : in n_samples x p x n, out n_samples x n
    Us = np.zeros((n_samples, n), dtype=np.complex128)
    for i in range(n_samples):
        Us[i] = compute_poly_sum(U[i], PolyW)

    # Add noise
    # noise = noise_level * np.random.randn(n_samples, n) + 1j*noise_level * np.random.randn(n_samples, n)
    # y += noise
    
    return x, Us


In [89]:
# Example usage
n_samples = 10000

# p : polynomial degree 
# k : influence scope 
# m : output dimension  
# n : input dimension 
p,k,m,n = 3, 2, 3, 2

true_coefficients = [0,1]

### part 1 : poly layer 
true_coefficients[1] = np.random.randn(p) + 1j*np.random.randn(p)
poly_power_limit = 0.05


### part 2 : conv layer k x m x n
true_coefficients[0] = np.random.randn(k, m, n) + 1j*np.random.randn(k, m, n)
noise_level = 0.05


x, y = generate_data(n_samples, true_coefficients, noise_level,poly_power_limit)

print("Input signal:", x[9])
print("Desired signal:", y[9])

[[[ 0.000e+00+0.000e+00j  0.000e+00+0.000e+00j]
  [ 0.000e+00+0.000e+00j  0.000e+00+0.000e+00j]
  [ 0.000e+00+0.000e+00j  0.000e+00+0.000e+00j]]

 [[ 0.000e+00+0.000e+00j  0.000e+00+0.000e+00j]
  [ 0.000e+00+0.000e+00j  0.000e+00+0.000e+00j]
  [ 0.000e+00+0.000e+00j  0.000e+00+0.000e+00j]]

 [[-2.079e+00-8.880e+00j -7.276e-01-6.486e+00j]
  [-4.324e-01-1.846e+00j -7.749e-02-6.908e-01j]
  [-8.990e-02-3.839e-01j -8.253e-03-7.357e-02j]]

 [[-4.669e-01+2.186e+00j  2.786e-01+1.667e+00j]
  [-5.831e-03+2.730e-02j  1.989e-03+1.189e-02j]
  [-7.282e-05+3.409e-04j  1.419e-05+8.490e-05j]]

 [[ 5.376e-01+7.862e-01j -1.085e+00+5.017e+00j]
  [ 1.219e-03+1.783e-03j -7.149e-02+3.305e-01j]
  [ 2.765e-06+4.044e-06j -4.709e-03+2.177e-02j]]

 [[ 8.873e-01-2.794e+00j -5.830e-01-2.839e+00j]
  [ 1.907e-02-6.006e-02j -1.224e-02-5.959e-02j]
  [ 4.098e-04-1.291e-03j -2.569e-04-1.251e-03j]]

 [[-4.358e+00-5.265e+00j  1.660e+00+7.097e-01j]
  [-5.089e-01-6.148e-01j  1.353e-02+5.784e-03j]
  [-5.943e-02-7.179e-02j  1.

In [90]:
## LMS filter

def lms_filter(x, y, k, mu, p, true_coefficients):
    Ws = [] 
    m, n = x.shape[1], y.shape[1]

    ConvW = np.random.randn(k, m, n) + 1j*np.random.randn(k, m, n)
    PolyW = np.random.randn(p) + 1j*np.random.randn(p)

    # backdoor 
    PolyW = true_coefficients[1]  
    ConvW = true_coefficients[0]

    ## iteration
    epoch = 5
    for _ in range(epoch):
        for i in range(k, len(x)):
            ### compute the error 
            C = compute_conv(x[i-k+1 : i+1], ConvW)
            u =  compute_poly(C,n,p,poly_power_limit)
            y_hat = compute_poly_sum(u, PolyW)
            e = y_hat - y[i]
            print ("e_0", e)

            ## update the weights 
            ### update the poly weights


            Ws.append((ConvW.copy(), PolyW.copy()))
    return  Ws



In [91]:
### Example usage
Ws = lms_filter(x, y, k, mu, p, true_coefficients)

## print in 3 decimal places
np.set_printoptions(precision=3)

print("Estimated coefficients:", Ws[0][0])
print("True coefficients:", true_coefficients[0])

print("Estimated coefficients:", Ws[0][1])
print("True coefficients:", true_coefficients[1])

y_hat [-2.422-3.906j -1.758-2.65j ]
y [-2.422-3.906j -1.758-2.65j ]
y_hat [0.343+1.073j 0.541+0.662j]
y [0.343+1.073j 0.541+0.662j]
y_hat [0.435+0.211j 0.727+2.416j]
y [0.435+0.211j 0.727+2.416j]
y_hat [-0.31 -1.437j -0.961-1.091j]
y [-0.31 -1.437j -0.961-1.091j]
y_hat [-3.045-1.345j  0.907-0.106j]
y [-3.045-1.345j  0.907-0.106j]
y_hat [ 1.81 -2.394j -0.178-1.953j]
y [ 1.81 -2.394j -0.178-1.953j]
y_hat [-0.79 +2.692j -0.313+1.438j]
y [-0.79 +2.692j -0.313+1.438j]
y_hat [0.834+1.524j 0.338+0.632j]
y [0.834+1.524j 0.338+0.632j]
y_hat [-2.835-1.239j -1.185-0.126j]
y [-2.835-1.239j -1.185-0.126j]
y_hat [-1.7 -0.231j -1.21-1.119j]
y [-1.7 -0.231j -1.21-1.119j]
y_hat [ 0.038+2.326j -2.395+0.628j]
y [ 0.038+2.326j -2.395+0.628j]
y_hat [2.899+0.012j 2.022+1.136j]
y [2.899+0.012j 2.022+1.136j]
y_hat [-1.569+1.824j  1.036+1.896j]
y [-1.569+1.824j  1.036+1.896j]
y_hat [-1.537-1.226j -1.321+0.486j]
y [-1.537-1.226j -1.321+0.486j]
y_hat [3.104+0.165j 1.494-1.326j]
y [3.104+0.165j 1.494-1.326j]
y_ha

In [92]:
print("Estimated coefficients:", Ws[-1][0])
print("True coefficients:", true_coefficients[0])

print("Estimated coefficients:", Ws[-1][1])
print("True coefficients:", true_coefficients[1])

Estimated coefficients: [[[-0.909-1.511j -0.592+0.645j]
  [ 0.188-0.981j -0.33 -0.857j]
  [-1.193-0.872j -0.205-0.423j]]

 [[-0.359+0.996j  0.603+0.712j]
  [-1.665+0.059j -0.7  -0.363j]
  [ 1.151+0.003j  1.857-0.106j]]]
True coefficients: [[[-0.909-1.511j -0.592+0.645j]
  [ 0.188-0.981j -0.33 -0.857j]
  [-1.193-0.872j -0.205-0.423j]]

 [[-0.359+0.996j  0.603+0.712j]
  [-1.665+0.059j -0.7  -0.363j]
  [ 1.151+0.003j  1.857-0.106j]]]
Estimated coefficients: [ 0.441-0.252j -0.331+0.11j   2.431+1.582j]
True coefficients: [ 0.441-0.252j -0.331+0.11j   2.431+1.582j]
